In [13]:
import evidently

In [14]:
from evidently.ui.workspace import Workspace

# Create a workspace and assign it a name
ws = Workspace.create("mlops")

In [15]:
project = ws.list_projects()[0] # get latest project

## Load Data

In [16]:
import pandas as pd

In [17]:
pd.read_csv("../data/test.csv")

transactionId                             basket customerType  \
0        4132523932                 [4, 3, 4, 3, 2, 3]     existing   
1        8998574539                    [3, 4, 4, 3, 5]     existing   
2        9346688547  [1, 1, 2, 2, 4, 4, 3, 1, 1, 0, 3]     existing   
3        4533897707           [3, 2, 2, 1, 5, 1, 1, 0]     existing   
4        3334800500              [4, 2, 3, 5, 2, 5, 1]     existing   
...             ...                                ...          ...   
9221     7995301628                             [1, 3]     existing   
9222     7387398375                       [1, 4, 3, 3]     existing   
9223     2777556607                                [4]     existing   
9224     7205276301              [4, 5, 4, 1, 0, 2, 0]     existing   
9225     2357221024                             [1, 4]     existing   

      totalAmount  returnLabel  
0           366.0            1  
1            85.0            0  
2           275.0            0  
3           528.0            0  
4           287.0            0  
...           ...          ...  
9221         66.0            0  
9222         40.0            0  
9223        126.0            1  
9224         70.0            0  
9225        142.0            0  

[9226 rows x 5 columns]

In [18]:
live_df = pd.read_csv("../data/live.csv")
live_df["orderedBooks"] = live_df["basket"].apply(lambda x: sum(c.isdigit() for c in x))
live_df

transactionId                             basket  totalAmount  \
0        4132523932                 [4, 3, 4, 3, 2, 3]        439.2   
1        8998574539                    [3, 4, 4, 3, 5]        102.0   
2        9346688547  [1, 1, 2, 2, 4, 4, 3, 1, 1, 0, 3]        330.0   
3        4533897707           [3, 2, 2, 1, 5, 1, 1, 0]        633.6   
4        3334800500              [4, 2, 3, 5, 2, 5, 1]        344.4   
...             ...                                ...          ...   
9221     7995301628                             [1, 3]         79.2   
9222     7387398375                       [1, 4, 3, 3]         48.0   
9223     2777556607                                [4]        151.2   
9224     7205276301              [4, 5, 4, 1, 0, 2, 0]         84.0   
9225     2357221024                             [1, 4]        170.4   

      orderedBooks  customerType_new  prediction  
0                6               0.0           1  
1                5               0.0           0  
2               11               0.0           0  
3                8               0.0           0  
4                7               0.0           0  
...            ...               ...         ...  
9221             2               0.0           0  
9222             4               0.0           0  
9223             1               0.0           1  
9224             7               0.0           0  
9225             2               0.0           0  

[9226 rows x 6 columns]

## Live Data Report

In [19]:
labels_df = pd.read_csv("../data/live_labels.csv")
labels_df

transactionId  returnLabel
0        4132523932            1
1        8998574539            0
2        9346688547            0
3        4533897707            0
4        3334800500            0
...             ...          ...
9221     7995301628            0
9222     7387398375            0
9223     2777556607            1
9224     7205276301            0
9225     2357221024            0

[9226 rows x 2 columns]

In [20]:
# join DFs
df_merged = live_df.merge(labels_df, on="transactionId", how="inner")
df_merged

transactionId                             basket  totalAmount  \
0        4132523932                 [4, 3, 4, 3, 2, 3]        439.2   
1        8998574539                    [3, 4, 4, 3, 5]        102.0   
2        9346688547  [1, 1, 2, 2, 4, 4, 3, 1, 1, 0, 3]        330.0   
3        4533897707           [3, 2, 2, 1, 5, 1, 1, 0]        633.6   
4        3334800500              [4, 2, 3, 5, 2, 5, 1]        344.4   
...             ...                                ...          ...   
9221     7995301628                             [1, 3]         79.2   
9222     7387398375                       [1, 4, 3, 3]         48.0   
9223     2777556607                                [4]        151.2   
9224     7205276301              [4, 5, 4, 1, 0, 2, 0]         84.0   
9225     2357221024                             [1, 4]        170.4   

      orderedBooks  customerType_new  prediction  returnLabel  
0                6               0.0           1            1  
1                5               0.0           0            0  
2               11               0.0           0            0  
3                8               0.0           0            0  
4                7               0.0           0            0  
...            ...               ...         ...          ...  
9221             2               0.0           0            0  
9222             4               0.0           0            0  
9223             1               0.0           1            1  
9224             7               0.0           0            0  
9225             2               0.0           0            0  

[9226 rows x 7 columns]

In [21]:
from evidently import BinaryClassification, Dataset, DataDefinition

current = DataDefinition(
    classification=[BinaryClassification(target="returnLabel", prediction_labels="prediction")],
    categorical_columns=["returnLabel", "prediction"]
)

eval_data = Dataset.from_pandas(
    df_merged,
    data_definition=current
)

## Classifciation Report

In [23]:
from evidently import Report
from evidently.presets import ClassificationPreset 

# Create a report
report = Report([ClassificationPreset()])

run = report.run(eval_data, None)
run

In [24]:
ws.add_run(project.id, run)

Report ID: 019a3488-8e87-74c3-8cbe-d0244f3820d9
Link: mlops/019a3486-5dd8-7be0-970a-e20328059ad5/snapshots/019a3488-8e87-74c3-8cbe-d0244f3820d9.json

## Data Summary

In [25]:
from evidently.presets import DataSummaryPreset 

report = Report([
    DataSummaryPreset(),
])

run2 = report.run(eval_data, None)
run2

In [ ]:
ws.add_run(project.id, run2)